# Choropleth map Netherlands' municipalities using Python's Bokeh with GEOJSON and CBS data
  
Looking at Bokeh's web page, you can find an example of plotting data in a regional map (http://bokeh.pydata.org/en/latest/docs/gallery/texas.html).  
In their case, they use data from Texas. However, trying to implement this for any other region is not as trivial as you might like.  
  
For this example, we make a map of the Netherlands, dividing it in all municipalities (Gemeenten). As input data we use free available CBS income data. 


In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

import matplotlib.pyplot as plt
plt.style.use('fivethirtyeight')
import seaborn as sns
from bokeh.io import output_notebook
from bokeh.plotting import figure, show


from bokeh.io import show, output_notebook
from bokeh.models import (
    GeoJSONDataSource,
    ColumnDataSource,
    HoverTool,
    LogColorMapper
)
from bokeh.palettes import Viridis6 as palette
from bokeh.plotting import figure

import json
from collections import OrderedDict
output_notebook()

import cbsodata

Loading BokehJS ...

## Get the data from CBS
For this, use the 'cbsodata' (https://pypi.python.org/pypi/cbsodata/0.1.1) package.  
You will need to install this.  
  
We load the data directly into a pandas dataframe

In [2]:
df_income = pd.DataFrame(cbsodata.get_data('80592NED'))

Retrieving data from table '80592NED'
Done!


In [3]:
# Take a look at the data from CBS:
df_income.head()

AantalHuishoudens_1  GemiddeldBesteedbaarInkomen_3  \
0               7247.5                           28.6   
1               7293.5                           30.0   
2               7350.9                           32.1   
3               7423.2                           32.8   
4               7497.5                           32.9   

   GemiddeldGestandaardiseerdInkomen_5 HoogteVanHetInkomen  ID  \
0                                 20.1  Totaal huishoudens   0   
1                                 21.0  Totaal huishoudens   1   
2                                 22.5  Totaal huishoudens   2   
3                                 23.0  Totaal huishoudens   3   
4                                 23.1  Totaal huishoudens   4   

   MediaanBesteedbaarInkomen_4  MediaanGestandaardiseerdInkomen_6  \
0                         24.8                               17.9   
1                         25.9                               18.7   
2                         27.2                               19.7   
3                         28.0                               20.3   
4                         28.1                               20.6   

                     Perioden     RegioS  RelatiefAantalHuishoudens_2  
0                        2005  Nederland                        100.0  
1                        2006  Nederland                        100.0  
2                        2007  Nederland                        100.0  
3                        2008  Nederland                        100.0  
4  2009 voor methodewijziging  Nederland                        100.0

In [4]:
# Only keep the income data from 2014 (the most recent). 
df_income = df_income[df_income['Perioden'] == '2014']

# CBS does something with upper quartile of local population and lower and etc. and etc. 
# We don't want all that, only keep full regional population
df_income = df_income[df_income['HoogteVanHetInkomen'] == 'Totaal huishoudens']

# Finally, there is an overload in columns we don't really need. Only keep the columns with region and average income.
df_income = df_income[['RegioS', 'GemiddeldBesteedbaarInkomen_3']]

# Decimals are weird from cbs for some reason
df_income['GemiddeldBesteedbaarInkomen_3'] = np.around(df_income['GemiddeldBesteedbaarInkomen_3'], decimals=0)

df_income = df_income[df_income['GemiddeldBesteedbaarInkomen_3'].notnull()]

# Set index for later purposes
df_income = df_income.set_index('RegioS')



In [5]:
# read all municipalities
with open(r'C:\Users\HR IPS\Documents\Python\Data\raw_input\Gemeenten.geojson', 'r') as f:
    dutch_municipalities_dict = json.loads(f.read(), object_hook=OrderedDict)

In [6]:
# See how this geojson looks. It's basically a dictionary with many polygons, 
# which dictate the outer edges of (in this case) the municipalities. 
# Also, there is an 'properties' part connected to each set of locations, which holds additional information. 
# Already included are the municipality names, code and some more features. 
# We will add one more feature ourselves here: the average regional income. 
dutch_municipalities_dict

OrderedDict([('type', 'FeatureCollection'),
             ('crs',
              OrderedDict([('type', 'name'),
                           ('properties',
                            OrderedDict([('name',
                                          'urn:ogc:def:crs:OGC:1.3:CRS84')]))])),
             ('features',
              [OrderedDict([('type', 'Feature'),
                            ('properties',
                             OrderedDict([('code', '1680'),
                                          ('name', 'Aa en Hunze'),
                                          ('regioFacet',
                                           'tcm:106-353398-1024'),
                                          ('level', 4),
                                          ('url',
                                           '/regioinformatie/gemeente/aa-en-hunze/')])),
                            ('geometry',
                             OrderedDict([('type', 'MultiPolygon'),
                                          (

In [37]:
# Some names we can fix, some not.
# You should really do this with a dictionary or something but at least this works

# This is an iterative process between this and the list 'unfindable' as defined below.
# This code needs to be run first though. 

df_income['GemiddeldBesteedbaarInkomen_3']['Dantumadeel (Dantumadiel)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Dantumadiel']
df_income['GemiddeldBesteedbaarInkomen_3']['Ferwerderadeel (Ferwerderadiel)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Ferwerderadiel']
df_income['GemiddeldBesteedbaarInkomen_3']['Littenseradeel (Littenseradiel)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Littenseradiel']
df_income['GemiddeldBesteedbaarInkomen_3']['Menaldumadeel (Menaldumadiel)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Menameradiel']
df_income['GemiddeldBesteedbaarInkomen_3']['SÃºdwest-FryslÃ¢n'] = df_income['GemiddeldBesteedbaarInkomen_3']['Súdwest-Fryslân']
df_income['GemiddeldBesteedbaarInkomen_3']['Tietjerksteradeel (Tytsjerksteradiel)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Tytsjerksteradiel']


df_income['GemiddeldBesteedbaarInkomen_3']['Bergen (L)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Bergen (L.)']
df_income['GemiddeldBesteedbaarInkomen_3']['Bergen (NH)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Bergen (NH.)']
df_income['GemiddeldBesteedbaarInkomen_3']['Utrecht (Ut)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Utrecht (gemeente)']
df_income['GemiddeldBesteedbaarInkomen_3']['Groningen (Gr)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Groningen (gemeente)']
df_income['GemiddeldBesteedbaarInkomen_3']['Beek'] = df_income['GemiddeldBesteedbaarInkomen_3']['Beek (L.)']
df_income['GemiddeldBesteedbaarInkomen_3']['Stein'] = df_income['GemiddeldBesteedbaarInkomen_3']['Stein (L.)']
df_income['GemiddeldBesteedbaarInkomen_3']['Hengelo (O)'] = df_income['GemiddeldBesteedbaarInkomen_3']['Hengelo (O.)']
df_income['GemiddeldBesteedbaarInkomen_3']['Middelburg'] = df_income['GemiddeldBesteedbaarInkomen_3']['Middelburg (Z.)']
df_income['GemiddeldBesteedbaarInkomen_3']['Rijswijk'] = df_income['GemiddeldBesteedbaarInkomen_3']['Rijswijk (ZH.)']
df_income['GemiddeldBesteedbaarInkomen_3']["'s-Gravenhage"] = df_income['GemiddeldBesteedbaarInkomen_3']["'s-Gravenhage (gemeente)"]
df_income['GemiddeldBesteedbaarInkomen_3']['Laren'] = df_income['GemiddeldBesteedbaarInkomen_3']['Laren (NH.)']


In [38]:
# Function below will add in the cbs data we have. 
# This is based on crossing the names: it will look for the name from the geojson in the cbs data
# This will work for many municipalities, but there will unfortunately be cases in which the municipality can't be found. 

# Python will give a KeyError in those cases. Because of changes in municipalities (Gemeentelijke herindelingen) 
# we won't be able to fix all name incompatabilities, but many we will. Therefore, store them in  a separate file. 

unfindable = []

def merge_income(dutch_municipalities_dict, df_income):
    
    municipality = dutch_municipalities_dict['properties']['name']
    
    try: 
        dutch_municipalities_dict['properties']['AverageIncome'] = round(df_income['GemiddeldBesteedbaarInkomen_3'][municipality],0).astype('float')
    except KeyError:
        unfindable.append(municipality)
        dutch_municipalities_dict['properties']['AverageIncome'] = 30.00

    return dutch_municipalities_dict

# merge income: execute the function here. 
dutch_municipalities_dict['features'] = [merge_income(municipality, df_income) for municipality in dutch_municipalities_dict['features']]

In [39]:
unfindable

['Maasdonk']

In [40]:
# Maasdonk is the only municipality we are unable to fix
# Some further research (i.e. Wikipedia) learns that this municipality has been assimilated during replanning. 

# Bokeh requires for all municipalities to have a value for AverageIncome. 
# We can't give this 0, since that would impact the map itself too much (it needs to have a color for the entire range)
# Therefore, we leave in the function that this municipality gets a value for AverageIncome of 30.0

df_income[df_income.index.str.contains('Maasdonk')]

Empty DataFrame
Columns: [GemiddeldBesteedbaarInkomen_3]
Index: []

# Visualization in Bokeh

In [41]:
geo_source = GeoJSONDataSource(geojson=json.dumps(dutch_municipalities_dict))

In [42]:
palette.reverse()

color_mapper = LogColorMapper(palette=palette)

TOOLS = "pan,wheel_zoom,box_zoom,reset,hover,save"

p = figure(
    title="Inkomen per gemeente", tools=TOOLS,
    x_axis_location=None, y_axis_location=None
)
p.grid.grid_line_color = None

p.patches('xs', 'ys', source=geo_source,
          fill_color={'field': 'AverageIncome', 'transform': color_mapper},
          fill_alpha=0.7, line_color="white", line_width=0.5)

hover = p.select_one(HoverTool)
hover.point_policy = "follow_mouse"
hover.tooltips = [
    ("Name", "@name"),
    ("Code", "@code"),
    ("AverageIncome", "@AverageIncome"),
    ("Level", "@level"),
    ("(Long, Lat)", "($x, $y)"),
]

show(p)

In [13]:
dutch_municipalities_dict

OrderedDict([('type', 'FeatureCollection'),
             ('crs',
              OrderedDict([('type', 'name'),
                           ('properties',
                            OrderedDict([('name',
                                          'urn:ogc:def:crs:OGC:1.3:CRS84')]))])),
             ('features',
              [OrderedDict([('type', 'Feature'),
                            ('properties',
                             OrderedDict([('code', '1680'),
                                          ('name', 'Aa en Hunze'),
                                          ('regioFacet',
                                           'tcm:106-353398-1024'),
                                          ('level', 4),
                                          ('url',
                                           '/regioinformatie/gemeente/aa-en-hunze/'),
                                          ('AverageIncome', 37.0)])),
                            ('geometry',
                             OrderedDict([('